In [3]:
from DBSCANSupport import DBSCANSupport
import pandas as pd
import numpy as np
from pathlib import Path
import plotly.express as px
from SeamountHelp import *

In [4]:
seamounts = pd.read_excel(Path('data') / 'sample_mask.txt.xlsx')

In [5]:
grav_dat = Path('data') / 'test_curv_32.highpass.csv'
grav = pd.read_csv(grav_dat, names=['Longitude', 'Latitude', 'Intensity'], header=0)
grav = grav[['Longitude', 'Latitude', 'Intensity']]
old_train_bounds = (-4.525, -2.38, -95.85833, -93.00833)

In [6]:
grav["Latitude"].describe()

count    720000.000000
mean         -5.000000
std           2.886749
min          -9.991667
25%          -7.495833
50%          -5.000000
75%          -2.504167
max          -0.008333
Name: Latitude, dtype: float64

In [7]:
grav["Longitude"].describe()

count    720000.000000
mean        -90.000000
std           5.773505
min         -99.991667
25%         -94.995833
50%         -90.000000
75%         -85.004167
max         -80.008333
Name: Longitude, dtype: float64

In [8]:
new_bounds = (-3, 0, -99, -96)
data = DBSCANSupport.formatData(grav, "Intensity")
test_params = (0.32052631578947366, 13)
best_eps = test_params[:1]
best_samp = test_params[1:]
tester = DBSCANSupport(Path('data') / "sample_mask.txt.xlsx", train_zone=new_bounds)

/Users/martinhawks/Code/Git_repos/stable_seamount/seamount_picking/code/_SeamountSupport.py:315: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data.loc[:, "TrueSeamount"] = np.zeros(data.shape[0])


In [9]:
tester.addTrainingData(data)
_, _, data_out, out = tester.gridSearch(best_eps, best_samp, verbose=True)

Score for 0.32052631578947366 and 13 is 0.612964599302579 with 4 clusters
Best score: 0.612964599302579 with parameters (0.32052631578947366, 13)


In [10]:
dfout = pd.DataFrame(data_out, columns=["Lat", "Lon", "Label", "Intensity", "TrueLabel"])
seamount_points = tester.getSeamountPoints()
df_labeled = dfout[(dfout["Label"] != dfout["Label"].mode().iloc[0])]

In [11]:
test_zone=new_bounds
seamounts = pd.read_excel(Path('data') / "sample_mask.txt.xlsx", \
                              sheet_name="new mask")
seamounts = seamounts.drop(columns=["VGG Height", "Radius", "base_depth", "-",
                                        "Name", "Charted", "surface_depth"])
seamounts = seamounts[(seamounts["Latitude"] >= test_zone[0]) & (seamounts["Latitude"] <= test_zone[1]) &
                          (seamounts["Longitude"] >= test_zone[2]) & (seamounts["Longitude"] <= test_zone[3])]
seamounts = seamounts.to_numpy()

In [12]:
fig = px.scatter(x=seamounts[:, 0], y=seamounts[:, 1], width=1000, height=500)
fig.add_trace(px.scatter(df_labeled, x="Lon", y="Lat", color="TrueLabel",).data[0])
fig.update_xaxes(
    scaleanchor="y",
    scaleratio=1,
  )
fig.update_layout(title="Model labels")
# fig.show()

In [13]:
raw_test_zone = grav[
    (
        grav["Latitude"] <= new_bounds[1]
    ) & (
        grav["Latitude"] >= new_bounds[0]
    ) & (
        grav["Longitude"] <= new_bounds[3]
    ) & (
        grav["Longitude"] >= new_bounds[2]
    )]

In [14]:
plotData(raw_test_zone)

In [15]:
larger_bounds = (2.574, 5.692, -105.077, -100.277)
with open(Path('data') / 'curv_32.highpass.xyz', 'r') as fin:
    newbound_data = readCroppedxyz(fin, larger_bounds)

In [16]:
newbound_data

array([[   5.69166667, -105.075     ,    4.80594444],
       [   5.69166667, -105.05833333,    1.89808118],
       [   5.69166667, -105.04166667,   -0.97615182],
       ...,
       [   2.575     , -100.325     ,    6.11869621],
       [   2.575     , -100.30833333,    4.15597868],
       [   2.575     , -100.29166667,   12.18155861]])

In [17]:
newbound_data = pd.DataFrame(newbound_data, columns=["Longitude", "Latitude", "Intensity"])
newbound_data = newbound_data[["Latitude", "Longitude", "Intensity"]]

In [18]:
plotData(newbound_data)

In [19]:
new_labels = tester.testData(newbound_data.to_numpy())

In [20]:
dfout = pd.DataFrame(new_labels, columns=["Latitude", "Longitude", "Label", "Intensity"])
df_labeled = dfout[(dfout["Label"] != dfout["Label"].mode().iloc[0])]
dfout = dfout.to_numpy()

In [21]:
plotData(df_labeled)

In [22]:
newtest = DBSCANSupport(Path('data') / "sample_mask.txt.xlsx", train_zone=larger_bounds)
test_trainer = newbound_data[["Latitude", "Longitude", "Intensity"]]
test_trainer_formated = newtest.formatData(test_trainer, "Intensity")
assert test_trainer_formated.shape[0] == test_trainer.shape[0]
newtest.addTrainingData(test_trainer_formated)
newtest.training_data.shape
true_lables = newtest.training_data[:, 3]

ValueError: Found array with 0 sample(s) (shape=(0, 4)) while a minimum of 1 is required by StandardScaler.

In [ ]:
lableled_out = np.insert(new_labels, 4, true_lables, axis=1)
lableled_out = pd.DataFrame(lableled_out, columns=["Latitude", "Longitude", "Lables", "Intensity", "TrueLabel"])
%load_ext autoreload
%autoreload 2

In [ ]:
plot = lableled_out[lableled_out["Lables"] != lableled_out["Lables"].mode().iloc[0]]
newbound_plot = plotData(plot, "TrueLabel")
seamounts = newtest.filterData(Path('data') / 'sample_mask.txt.xlsx', larger_bounds)
newbound_plot.add_trace(px.scatter(seamounts, x="Longitude", y="Latitude").data[0])
newbound_plot.data = newbound_plot.data[::-1]


In [ ]:
#newbound_plot.add_trace(px.scatter(newbound_data, x="Longitude", y="Latitude", color="Intensity", opacity=0.5).data[0])
newbound_plot.show()

In [ ]:
raw_newbound = plotData(newbound_data, op=1)
raw_newbound.add_trace(newbound_plot.data[1])
raw_newbound.show()

In [23]:
with open (Path('data') / 'curv_32.highpass.xyz', 'r') as fin:
    large_raw = readCroppedxyz(fin, (14, 15, -101, -100))

In [24]:
plotData(pd.DataFrame(large_raw, columns=['Longitude', 'Latitude', 'Intensity']))

In [25]:
plotTestZone((14, 15, -101, -100), large_raw)

In [26]:
tested = testNewZone((14, 15, -101, -100), large_raw).drop(columns='TrueVal')
tested = tested[tested["Cluster"] != tested['Cluster'].mode()[0]]
tested = tested[tested['Intensity'] >= 0]

In [27]:
reformated, centers = divClusters(tested.to_numpy())

In [28]:
exportCentroids(centers)